In [1]:
# Import packages
library(rstan)
library(coda)
library(parallel)
library(Bessel)

Loading required package: StanHeaders
Loading required package: ggplot2
Registered S3 methods overwritten by 'ggplot2':
  method         from 
  [.quosures     rlang
  c.quosures     rlang
  print.quosures rlang
rstan (Version 2.19.2, GitRev: 2e1f913d3ca3)
For execution on a local, multicore CPU with excess RAM we recommend calling
options(mc.cores = parallel::detectCores()).
To avoid recompilation of unchanged Stan programs, we recommend calling
rstan_options(auto_write = TRUE)
For improved execution time, we recommend calling
Sys.setenv(LOCAL_CPPFLAGS = '-march=native')
although this causes Stan to throw an error on a few processors.

Attaching package: 'coda'

The following object is masked from 'package:rstan':

    traceplot



In [2]:
# add path required by rstan
library(devtools) 
Sys.setenv(PATH = paste("C:/Rtools/bin", Sys.getenv("PATH"), sep=";")) 
Sys.setenv(PATH = paste("C:\\Rtools\\mingw_64\\bin", Sys.getenv("PATH"), sep=";")) 
Sys.setenv(BINPREF = "C:/Rtools/mingw_$(WIN)/bin/")

Loading required package: usethis


# Read csv into dataframe

In [3]:
dat.str <- Sys.glob("data.*.csv")
data <- as.data.frame(read.csv(file = dat.str))
# slicing training set (whole 2018 season)
dat <- data[data$period < 25,]

In [4]:
head(dat)

X   Date       Season round period home.name away.name home.score
172 190 2018-03-25 2018   1     24     WC        SY         86       
173 191 2018-03-25 2018   1     24     ME        GE         94       
174 192 2018-03-25 2018   1     24     GW        WB        133       
175 193 2018-03-24 2018   1     24     GC        NM         55       
176 194 2018-03-24 2018   1     24     HW        CW        101       
177 195 2018-03-24 2018   1     24     PA        FR        110       
    away.score home.goals ... Total.Score.Over.Min Total.Score.Over.Max
172 115        13         ... 1.813                1.925               
173  97        13         ... 1.813                1.925               
174  51        20         ... 1.925                1.925               
175  39         7         ... 1.961                1.961               
176  67        15         ... 1.925                1.909               
177  60        16         ... 1.925                1.862               
    Total.Score.Over.Close Total.Score.Under.Open Total.Score.Under.Min
172 1.892                  1.925                  1.925                
173 1.925                  1.925                  1.925                
174 1.925                  1.925                  1.925                
175 1.961                  1.925                  1.892                
176 1.840                  1.925                  1.925                
177 1.862                  1.925                  1.925                
    Total.Score.Under.Max Total.Score.Under.Close Notes home.number away.number
172 2.050                 1.961                         10          17         
173 1.925                 1.925                          4          11         
174 1.925                 1.925                          2          12         
175 1.990                 1.892                         16           3         
176 2.020                 2.020                          8           9         
177 1.990                 1.990                         13           7

In [5]:
# library(hash)

# h <- hash()

# for (i in 1:length(sort(unique(dat$home.name)))){
#     h[[as.character(sort(unique(dat$home.name))[i])]] <- i
# }

In [82]:
# library(hash)

# h <- hash()

# for (i in 1:length(sort(unique(dat$home.name)))){
#     h[[as.character(sort(unique(dat$home.name))[i])]] <- i
# }

# home.number <- vector()
# away.number <- vector()

# for (i in 1:nrow(dat)){
#     home.number <- append(home.number, h[[as.character(dat$home.name[i])]])
#     away.number <- append(away.number, h[[as.character(dat$away.name[i])]])
    
# }

# dat$home.number <- home.number
# dat$away.number <- away.number

In [84]:
# write.csv(dat, 'temp.csv')

# 2019 Round 1 data

In [5]:
matchup <- data[data$period == 25,]
n.matches <- length(matchup$home.number)
matchup

X   Date       Season round period home.name away.name home.score
163 181 2018-04-02 2018   2     25     GE        HW        117       
164 182 2018-04-01 2018   2     25     SY        PA         71       
165 183 2018-04-01 2018   2     25     WB        WC         70       
166 184 2018-03-31 2018   2     25     FR        ES        106       
167 185 2018-03-31 2018   2     25     BL        ME         74       
168 186 2018-03-31 2018   2     25     CW        GW         79       
169 187 2018-03-31 2018   2     25     CA        GC         67       
170 188 2018-03-30 2018   2     25     NM        SK         95       
171 189 2018-03-29 2018   2     25     AD        RI        118       
    away.score home.goals ... Total.Score.Over.Min Total.Score.Over.Max
163 118        18         ... 1.840                1.925               
164  94        10         ... 1.854                1.925               
165 121         9         ... 1.813                2.200               
166  90        16         ... 1.877                1.925               
167 100        10         ... 1.925                1.925               
168  95        12         ... 1.925                1.925               
169 101         9         ... 1.909                2.050               
170  43        13         ... 1.943                1.934               
171  82        18         ... 1.909                1.925               
    Total.Score.Over.Close Total.Score.Under.Open Total.Score.Under.Min
163 1.840                  1.925                  1.925                
164 1.892                  1.925                  1.925                
165 1.934                  1.925                  1.925                
166 1.877                  1.925                  1.925                
167 1.925                  1.925                  1.925                
168 2.000                  1.925                  1.854                
169 1.909                  1.925                  1.943                
170 1.943                  1.925                  1.909                
171 1.925                  1.925                  1.840                
    Total.Score.Under.Max Total.Score.Under.Close Notes home.number away.number
163 2.020                 2.020                          1          16         
164 1.961                 1.961                         17          13         
165 1.925                 1.917                          4           8         
166 1.990                 1.980                          9          18         
167 1.925                 1.925                          7           5         
168 1.925                 1.854                          3          10         
169 1.925                 1.943                         11           2         
170 1.925                 1.909                         15          12         
171 1.925                 1.925                          6          14

# Data

In [6]:
home.name <- as.matrix(dat$home.name)
away.name <- as.matrix(dat$away.name)
home.numb <- dat$home.number
away.numb <- dat$away.number

home.Goals <- dat$home.goals
home.Behinds <- dat$home.behinds
away.Goals <- dat$away.goals
away.Behinds <- dat$away.behinds

period <- dat$period
n.teams <- 18
n.games <- length(home.numb)
n.periods <- max(period)
n.bps <- 2
bps <- c(1,24)

In [7]:
# matricies for the Owen paper centering
ones <- matrix(1, nrow = (n.teams-1), ncol = 1)
S_t <-  n.teams / (n.teams-1) * (diag(n.teams-1) + ones %*% t(ones))

# Jmat is n * n-1
J.up.left <- diag(n.teams-1) - (1/n.teams)*(ones %*% t(ones))
J.bot.left <- - t(ones) * 1/n.teams

Jmat <- rbind(J.up.left, J.bot.left)

# Store data into list required by STAN

In [8]:
dat.list <- list(N = n.teams,
                 G = n.games,
                 T = n.periods,
                 period = period,
                 home = home.numb,
                 away = away.numb,
                 homeGoals = home.Goals,
                 homeBehinds = home.Behinds,
                 awayGoals = away.Goals,
                 awayBehinds = away.Behinds,
                 BP = n.bps,
                 Breaks = bps,
                 Smat = S_t,
                 JmatTrans = t(Jmat),
                 N_Matches = n.matches,
                 nextHome = matchup$home.number,
                 nextAway = matchup$away.number)

# Compile the model

In [9]:
prefit <- stan("Skellam goal and behind difference.stan", data = dat.list, chains = 0)

DIAGNOSTIC(S) FROM PARSER:
Info: Comments beginning with # are deprecated.  Please use // in place of # for line comments.
Info: assignment operator <- deprecated in the Stan language; use = instead.
Info: Comments beginning with # are deprecated.  Please use // in place of # for line comments.
Info: Comments beginning with # are deprecated.  Please use // in place of # for line comments.
Info: Comments beginning with # are deprecated.  Please use // in place of # for line comments.
Info: Comments beginning with # are deprecated.  Please use // in place of # for line comments.
Info: Comments beginning with # are deprecated.  Please use // in place of # for line comments.
Info: Comments beginning with # are deprecated.  Please use // in place of # for line comments.
Info: Comments beginning with # are deprecated.  Please use // in place of # for line comments.
Info: Comments beginning with # are deprecated.  Please use // in place of # for line comments.
Info: Comments beginning with # 

the number of chains is less than 1; sampling not done


# Sampling using MCMC (4 cores in parallel)

In [10]:
cl <- makeCluster(4)

clusterEvalQ(cl, library(rstan))

myfunction <- function(var1, var2, var3){
    stan(fit = var3, data = var2,
                            chains = 1, chain_id = var1, iter = 2500,
                            refresh = -1, init = "0")
}

sflist <- parLapply(cl, 1:4, fun = myfunction, var2 = dat.list, var3 = prefit)
stopCluster(cl)

[[1]]
 [1] "rstan"       "ggplot2"     "StanHeaders" "stats"       "graphics"   
 [6] "grDevices"   "utils"       "datasets"    "methods"     "base"       

[[2]]
 [1] "rstan"       "ggplot2"     "StanHeaders" "stats"       "graphics"   
 [6] "grDevices"   "utils"       "datasets"    "methods"     "base"       

[[3]]
 [1] "rstan"       "ggplot2"     "StanHeaders" "stats"       "graphics"   
 [6] "grDevices"   "utils"       "datasets"    "methods"     "base"       

[[4]]
 [1] "rstan"       "ggplot2"     "StanHeaders" "stats"       "graphics"   
 [6] "grDevices"   "utils"       "datasets"    "methods"     "base"

In [11]:
sflist

[[1]]
Inference for Stan model: Skellam goal and behind difference.
1 chains, each with iter=2500; warmup=1250; thin=1; 
post-warmup draws per chain=1250, total post-warmup draws=1250.

                           mean se_mean     sd    2.5%    25%    50%    75%
delta                      0.69    0.00   0.07    0.54   0.64   0.69   0.74
attackGoals_raw[1,1]       1.71    0.10   2.72   -4.05   0.00   1.67   3.52
attackGoals_raw[1,2]      -4.87    0.09   2.71   -8.88  -7.00  -5.17  -3.16
attackGoals_raw[1,3]      -3.57    0.11   3.23   -8.86  -6.02  -3.90  -1.31
attackGoals_raw[1,4]      -0.22    0.12   3.10   -6.43  -2.39  -0.15   2.10
attackGoals_raw[1,5]       0.43    0.09   2.54   -4.64  -1.35   0.51   2.06
attackGoals_raw[1,6]       0.81    0.10   2.92   -5.27  -1.11   0.87   2.87
attackGoals_raw[1,7]      -0.21    0.09   2.49   -5.17  -1.93  -0.22   1.50
attackGoals_raw[1,8]       1.19    0.10   2.63   -4.10  -0.47   1.19   3.01
attackGoals_raw[1,9]       1.15    0.07   1.91   -2.38

In [11]:
fit <- sflist2stanfit(sflist)

In [12]:
write.csv(print(summary(fit)), file = "fitproper.csv")

$summary
                                  mean      se_mean           sd          2.5%
delta                     8.824045e-01 0.0015770217 7.321102e-02  7.383862e-01
attackGoals_raw[1,1]      1.955663e+00 0.0660164253 2.582200e+00 -2.992525e+00
attackGoals_raw[1,2]     -1.527986e+00 0.0632513535 3.189473e+00 -7.646519e+00
attackGoals_raw[1,3]      1.447861e+00 0.0696971601 2.941512e+00 -4.403547e+00
attackGoals_raw[1,4]     -2.125639e+00 0.0608696561 2.762484e+00 -7.256749e+00
attackGoals_raw[1,5]      1.154403e+00 0.0614375786 3.140830e+00 -5.204349e+00
attackGoals_raw[1,6]      8.529665e-01 0.0638645290 2.893435e+00 -4.706611e+00
attackGoals_raw[1,7]      1.122229e+00 0.0637671370 2.933417e+00 -4.578572e+00
attackGoals_raw[1,8]      2.616844e-02 0.0515230957 2.723327e+00 -5.412610e+00
attackGoals_raw[1,9]      1.220401e-01 0.0691366652 3.088548e+00 -6.100865e+00
attackGoals_raw[1,10]    -3.156322e+00 0.0659211678 3.343232e+00 -8.645865e+00
attackGoals_raw[1,11]     1.785849e+00 0.08

# Extract parameters

In [13]:
fit.samples <- extract(fit)
write.csv(fit.samples, file = "samples.csv")

# Take the average of the mu for each team

In [14]:
# parameter estimate extractor
delta <- mean (fit.samples$delta)
muAttGoals.vec <- apply(fit.samples$muAttGoals, 2, mean) # I think the 18th team here is
  # suffering from the sum to zero constraint, maybe will dissapear with more samples

muAttBehinds.vec <- apply(fit.samples$muAttBehinds, 2, mean)
muDef.vec <- apply(fit.samples$muDef, 2, mean)

mu.ests <- matrix(c( "Goal attack mean estimates", muAttGoals.vec,"Behind attack mean estimates", muAttBehinds.vec,
                     "defend means estimates", muDef.vec), ncol = 3, byrow = F)
write.csv(mu.ests, file = "AR mean estimates.csv")

# Extract phiAtt, phiDef, attackGoals, attackBehinds, defend

In [15]:
phiAtt.vec <- mean(fit.samples$phiAtt)
phiDef.vec <- mean(fit.samples$phiDef)
std.attack.vec <- mean(fit.samples$stdAtt)
std.def.vec <- mean(fit.samples$stdDef)

goal.attack.strenghts.mat <- apply(fit.samples$attackGoals, 2:3, mean)
write.csv(goal.attack.strenghts.mat, file = "goal.attack.str.csv")

behind.attack.strengths.mat <- apply(fit.samples$attackBehinds, 2:3, mean)
write.csv(behind.attack.strengths.mat, file = "behind.attack.str.csv")

defence.strengths.mat <- apply(fit.samples$defend, 2:3, mean)
write.csv(defence.strengths.mat, file = "def.str.csv")

par.vec <- c(delta, "delta",
             phiAtt.vec, "phi.attack",
             phiDef.vec, "phi.defend",
             std.attack.vec, "std.attack",
             std.def.vec, "std.defend")

par.vec.est <- matrix(par.vec, ncol = 2, byrow = T)
write.csv(par.vec.est,  file = "parameter estimates.csv")

# Extract goalDiff, behindDiff, and totalDiff

In [16]:
avg.pred.goal.diff <- apply(fit.samples$goalDiff, 2, mean)
avg.pred.behind.diff <- apply(fit.samples$behindDiff, 2, mean)
avg.pred.total.diff <- apply(fit.samples$totalDiff, 2, mean)

In [17]:
# see if we got it right
actual.total.diff <- matchup$home.score - matchup$away.score
correct.vec <- ((avg.pred.total.diff * actual.total.diff)>0)

In [18]:
actual.total.diff
correct.vec

[1]  -1 -23 -51  16 -26 -16 -34  52  36

[1] FALSE FALSE FALSE FALSE  TRUE FALSE FALSE  TRUE  TRUE

# Calculate percentage of win, loss and draw

In [19]:
# get the percentage of win/loss

winDrawLossPer <- function(x.vec) {
  home.win.per <- mean(as.numeric(x.vec > 0))
  draw.per <- mean(as.numeric(x.vec == 0))
  away.win.per <- mean(as.numeric(x.vec < 0))
  c(home.win.per, draw.per ,away.win.per)
}

In [20]:
per.chance.mat <- apply(fit.samples$totalDiff, 2, winDrawLossPer)
per.chance.mat

iterations [,1]   [,2]   [,3]   [,4]   [,5]   [,6]   [,7]   [,8]   [,9]  
      [1,] 0.5396 0.8282 0.5660 0.2252 0.2910 0.8224 0.5702 0.9596 0.5352
      [2,] 0.0522 0.0258 0.0276 0.0304 0.0284 0.0248 0.0320 0.0050 0.0746
      [3,] 0.4082 0.1460 0.4064 0.7444 0.6806 0.1528 0.3978 0.0354 0.3902

In [21]:
# the sd ests are going to be wildly larger than they should due to not throwing out burn in
# samples, should probably change all my apply's to deal with this but ehhhhhhhh, more samples
# takes care of it for the most part
sd.ests <- round(apply(fit.samples$totalDiff,2,sd),2)

In [22]:
sim.pred.mat <- matrix(c("behind diff", avg.pred.behind.diff,
                         "goal diff", avg.pred.goal.diff,
                         "total diff", avg.pred.total.diff,
                         "home team", as.character(matchup$home.name),
                         "away team", as.character(matchup$away.name),
                         "actual result", actual.total.diff,
                         "prediction correct?", correct.vec,
                         "home win prob", per.chance.mat[1,],
                         "draw prob", per.chance.mat[2,],
                         "home loss prob", per.chance.mat[3,],
                         "simulated sd ests", sd.ests
                         ), nrow = 11, byrow = T)

write.csv(sim.pred.mat, file = "internal predictions.csv")

In [23]:
sim.pred.mat

[,1]                [,2]   [,3]    [,4]   [,5]     [,6]     [,7]   
 [1,] behind diff         1.234  2.02    4.1776 -6.8398  -0.1794  1.6394 
 [2,] goal diff           0.86   8.1524  0.1596 -1.2258  -3.1012  6.0062 
 [3,] total diff          6.394  50.9344 5.1352 -14.1946 -18.7866 37.6766
 [4,] home team           GE     SY      WB     FR       BL       CW     
 [5,] away team           HW     PA      WC     ES       ME       GW     
 [6,] actual result       -1     -23     -51    16       -26      -16    
 [7,] prediction correct? FALSE  FALSE   FALSE  FALSE    TRUE     FALSE  
 [8,] home win prob       0.5396 0.8282  0.566  0.2252   0.291    0.8224 
 [9,] draw prob           0.0522 0.0258  0.0276 0.0304   0.0284   0.0248 
[10,] home loss prob      0.4082 0.146   0.4064 0.7444   0.6806   0.1528 
[11,] simulated sd ests   28.33  80.61   56.72  30.78    61.17    65.87  
      [,8]    [,9]    [,10] 
 [1,] 2.561   11.9912 0.2304
 [2,] 2.0658  11.2446 1.1062
 [3,] 14.9558 79.4588 6.8676
 [4,] CA      NM      AD    
 [5,] GC      SK      RI    
 [6,] -34     52      36    
 [7,] FALSE   TRUE    TRUE  
 [8,] 0.5702  0.9596  0.5352
 [9,] 0.032   0.005   0.0746
[10,] 0.3978  0.0354  0.3902
[11,] 55.9    105.25  34.44

In [24]:
write.csv(t(sim.pred.mat),  file = "round2_prediction.csv")